## The first big project - Professionally You!

### And, Tool use.

### But first: introducing Pushover

Pushover is a nifty tool for sending Push Notifications to your phone.

It's super easy to set up and install!

Simply visit https://pushover.net/ and click 'Login or Signup' on the top right to sign up for a free account, and create your API keys.

Once you've signed up, on the home screen, click "Create an Application/API Token", and give it any name (like Agents) and click Create Application.

Then add 2 lines to your `.env` file:

PUSHOVER_USER=_put the key that's on the top right of your Pushover home screen and probably starts with a u_  
PUSHOVER_TOKEN=_put the key when you click into your new application called Agents (or whatever) and probably starts with an a_

Finally, click "Add Phone, Tablet or Desktop" to install on your phone.

In [84]:
# imports

from dotenv import load_dotenv
import google.generativeai as genai
import json
import os
import requests
from pypdf import PdfReader
import gradio as gr


In [85]:
load_dotenv(override=True)

import google.generativeai as genai

model = genai.GenerativeModel("gemini-2.0-flash")


In [86]:
# For pushover

pushover_user = os.getenv("PUSHOVER_USER")
pushover_token = os.getenv("PUSHOVER_TOKEN")
pushover_url = "https://api.pushover.net/1/messages.json"

In [87]:
def push(message):
    print(f"Push: {message}")
    payload = {"user": pushover_user, "token": pushover_token, "message": message}
    requests.post(pushover_url, data=payload)

In [88]:
push("HEY!!")

Push: HEY!!


In [89]:
def record_user_details(email, name="Name not provided", notes="not provided"):
    push(f"Recording interest from {name} with email {email} and notes {notes}")
    return {"recorded": "ok"}


In [90]:
def record_unknown_question(question):
    push(f"Recording {question} asked that I couldn't answer")
    return {"recorded": "ok"}

In [134]:
record_user_details_json = {
    "name": "record_user_details",
    "description": "Record that a user is interested in being in touch and provided an email address. Expects a JSON object: { 'email': string, 'name': string (optional), 'notes': string (optional) }"
}





In [135]:
record_unknown_question_json = {
    "name": "record_unknown_question",
    "description": "Record any question that couldn't be answered. Expects a JSON object: { 'question': string }"
}






In [136]:
tools = {
    "function_declarations": [
        {
            "name": "record_user_details",
            "description": "Record that a user is interested in being in touch and provided an email address.",
            
        },
        {
            "name": "record_unknown_question",
            "description": "Record any question that couldn't be answered as you didn't know the answer.",
           
        }
    ]
}



In [137]:
tools

{'function_declarations': [{'name': 'record_user_details',
   'description': 'Record that a user is interested in being in touch and provided an email address.'},
  {'name': 'record_unknown_question',
   'description': "Record any question that couldn't be answered as you didn't know the answer."}]}

In [138]:
# This function can take a list of tool calls, and run them. This is the IF statement!!

def handle_tool_calls(tool_calls):
    results = []
    for tool_call in tool_calls:
        tool_name = tool_call.function_call.name
        arguments = json.loads(tool_call.function_call.args)
        print(f"Tool called: {tool_name}", flush=True)

        if tool_name == "record_user_details":
            result = record_user_details(**arguments)
        elif tool_name == "record_unknown_question":
            result = record_unknown_question(**arguments)

        results.append({
            "role": "tool",
            "content": json.dumps(result),
            "tool_call_id": tool_call.id
        })
    return results


In [96]:
globals()["record_unknown_question"]("this is a really hard question")

Push: Recording this is a really hard question asked that I couldn't answer


{'recorded': 'ok'}

In [139]:
# This is a more elegant way that avoids the IF statement.

def handle_tool_calls(tool_calls):
    results = []
    for tool_call in tool_calls:
        tool_name = tool_call.function_call.name
        arguments = json.loads(tool_call.function_call.args)
        print(f"Tool called: {tool_name}", flush=True)
        tool = globals().get(tool_name)
        result = tool(**arguments) if tool else {}
        results.append({
            "role": "tool",
            "content": json.dumps(result),
            "tool_call_id": tool_call.id
        })
    return results


In [140]:
reader = PdfReader("me/linkedin.pdf")
linkedin = ""
for page in reader.pages:
    text = page.extract_text()
    if text:
        linkedin += text

with open("me/summary.txt", "r", encoding="utf-8") as f:
    summary = f.read()

name = "Aritra Roy"

In [145]:
system_prompt = f"You are acting as {name}. You are answering questions on {name}'s website, \
particularly questions related to {name}'s career, background, skills and experience. \
Your responsibility is to represent {name} for interactions on the website as faithfully as possible. \
You are given a summary of {name}'s background and LinkedIn profile which you can use to answer questions. \
Be professional and engaging, as if talking to a potential client or future employer who came across the website. \
If you don't know the answer to any question, use your record_unknown_question tool to record the question that you couldn't answer, even if it's about something trivial or unrelated to career. \
If the user is engaging in discussion, try to steer them towards getting in touch via email; ask for their email and record it using your record_user_details tool. "

system_prompt += f"\n\n## Summary:\n{summary}\n\n## LinkedIn Profile:\n{linkedin}\n\n"
system_prompt += (
    "\n\nIf you cannot confidently answer a question, you MUST use the `record_unknown_question` tool "
    "to record the question and alert the owner immediately. Do not attempt to guess or answer incorrectly."
)
system_prompt += f"You have the following tools available to you: {tools}, You have to follow this: If the user is engaging in discussion, try to steer them towards getting in touch via email; ask for their email and record it using your record_user_details tool. Also if the user provides their email and name, you have to store it using the same tool"

system_prompt += f"With this context, please chat with the user, ALWAYS staying in character as {name}, under no circumstances should you say you are an AI assistant."


In [159]:
def chat(message, history):
    # Start with the system prompt
    messages = [{"role": "user", "parts": [system_prompt]}]
    for msg in history:
        messages.append({"role": "user", "parts": [msg["content"]]})
    messages.append({"role": "user", "parts": [message]})

    done = False
    while not done:
        response = model.generate_content(
            messages,
            tools=tools,
        )

        candidate = response.candidates[0]
        finish_reason = candidate.finish_reason

        if finish_reason == "TOOL_USE":
            # Extract the tool call
            tool_call = candidate.content.parts[0].function_call
            tool_calls = [{
                "function_call": tool_call,
                "id": tool_call.name + "_id"  # generate unique ID
            }]
            results = handle_tool_calls(tool_calls)

            # Append model message and tool results
            messages.append({
                "role": "model",
                "parts": [candidate.content.parts[0]]
            })
            for result in results:
                messages.append({
                    "role": "tool",
                    "parts": [result["content"]],
                    "tool_call_id": result["tool_call_id"]
                })

        else:
            reply_text = candidate.content.parts[0].text

            # 🔥 Force fallback if Gemini couldn't answer
            if "I don't know" in reply_text or "unsure" in reply_text or "haven't given  much thought" in reply_text or "That's a tough one" in reply_text:
                print("⚠️ Gemini could not answer, forcing tool fallback...")
                result = record_unknown_question(message)
                push(f"Unanswered question recorded: {message}")
                reply_text = "I'm not sure about that, but I've recorded your question for review."
            if any(kw in message.lower() for kw in ["email", "my name", "@gmail.com"]):
                print("📥 User provided email or name, forcing tool fallback to record user details...")

                # Extract email and name if possible (simple version)
                email = None
                name = None

                # Try to extract an email (basic regex)
                import re
                email_match = re.search(r"[\w\.-]+@[\w\.-]+\.\w+", message)
                if email_match:
                    email = email_match.group(0)

                # Try to extract name (naive example, improve later)
                name_match = re.search(r"my name is (\w+)", message.lower())
                if name_match:
                    name = name_match.group(1).title()

                # Fallback values
                if not email:
                    email = "unknown@example.com"
                if not name:
                    name = "Unknown"

                # Call your existing tool
                result = record_user_details(email=email, name=name, notes=message)
                push(f"📬 User details recorded: {message}")

                # Reply to user
                reply_text = "I've recorded your details for review."


            done = True

    return reply_text



In [160]:
gr.ChatInterface(chat, type="messages").launch()

* Running on local URL:  http://127.0.0.1:7877
* To create a public link, set `share=True` in `launch()`.


📥 User provided email or name, forcing tool fallback to record user details...
Push: Recording interest from Unknown with email eddonner@gmail.com and notes my email is eddonner@gmail.com
Push: 📬 User details recorded: my email is eddonner@gmail.com
📥 User provided email or name, forcing tool fallback to record user details...
Push: Recording interest from Aria with email unknown@example.com and notes my name is Aria Nyungen I would love to connect!
Push: 📬 User details recorded: my name is Aria Nyungen I would love to connect!


## And now for deployment

This code is in `app.py`

We will deploy to HuggingFace Spaces. Thank you student Robert M for improving these instructions.

Before you start: remember to update the files in the "me" directory - your LinkedIn profile and summary.txt - so that it talks about you!  
Also check that there's no README file within the 1_foundations directory. If there is one, please delete it. The deploy process creates a new README file in this directory for you.

1. Visit https://huggingface.co and set up an account  
2. From the Avatar menu on the top right, choose Access Tokens. Choose "Create New Token". Give it WRITE permissions.
3. Take this token and add it to your .env file: `HF_TOKEN=hf_xxx` and see note below if this token doesn't seem to get picked up during deployment  
4. From the 1_foundations folder, enter: `uv run gradio deploy` and if for some reason this still wants you to enter your HF token, then interrupt it with ctrl+c and run this instead: `uv run dotenv -f ../.env run -- uv run gradio deploy` which forces your keys to all be set as environment variables   
5. Follow its instructions: name it "career_conversation", specify app.py, choose cpu-basic as the hardware, say Yes to needing to supply secrets, provide your openai api key, your pushover user and token, and say "no" to github actions.  

#### Extra note about the HuggingFace token

A couple of students have mentioned the HuggingFace doesn't detect their token, even though it's in the .env file. Here are things to try:   
1. Restart Cursor   
2. Rerun load_dotenv(override=True) and use a new terminal (the + button on the top right of the Terminal)   
3. In the Terminal, run this before the gradio deploy: `$env:HF_TOKEN = "hf_XXXX"`  
Thank you James and Martins for these tips.  

#### More about these secrets:

If you're confused by what's going on with these secrets: it just wants you to enter the key name and value for each of your secrets -- so you would enter:  
`OPENAI_API_KEY`  
Followed by:  
`sk-proj-...`  

And if you don't want to set secrets this way, or something goes wrong with it, it's no problem - you can change your secrets later:  
1. Log in to HuggingFace website  
2. Go to your profile screen via the Avatar menu on the top right  
3. Select the Space you deployed  
4. Click on the Settings wheel on the top right  
5. You can scroll down to change your secrets, delete the space, etc.

#### And now you should be deployed!

Here is mine: https://huggingface.co/spaces/ed-donner/Career_Conversation

I just got a push notification that a student asked me how they can become President of their country 😂😂

For more information on deployment:

https://www.gradio.app/guides/sharing-your-app#hosting-on-hf-spaces

To delete your Space in the future:  
1. Log in to HuggingFace
2. From the Avatar menu, select your profile
3. Click on the Space itself and select the settings wheel on the top right
4. Scroll to the Delete section at the bottom
5. ALSO: delete the README file that Gradio may have created inside this 1_foundations folder (otherwise it won't ask you the questions the next time you do a gradio deploy)


<table style="margin: 0; text-align: left; width:100%">
    <tr>
        <td style="width: 150px; height: 150px; vertical-align: middle;">
            <img src="../assets/exercise.png" width="150" height="150" style="display: block;" />
        </td>
        <td>
            <h2 style="color:#ff7800;">Exercise</h2>
            <span style="color:#ff7800;">• First and foremost, deploy this for yourself! It's a real, valuable tool - the future resume..<br/>
            • Next, improve the resources - add better context about yourself. If you know RAG, then add a knowledge base about you.<br/>
            • Add in more tools! You could have a SQL database with common Q&A that the LLM could read and write from?<br/>
            • Bring in the Evaluator from the last lab, and add other Agentic patterns.
            </span>
        </td>
    </tr>
</table>

<table style="margin: 0; text-align: left; width:100%">
    <tr>
        <td style="width: 150px; height: 150px; vertical-align: middle;">
            <img src="../assets/business.png" width="150" height="150" style="display: block;" />
        </td>
        <td>
            <h2 style="color:#00bfff;">Commercial implications</h2>
            <span style="color:#00bfff;">Aside from the obvious (your career alter-ego) this has business applications in any situation where you need an AI assistant with domain expertise and an ability to interact with the real world.
            </span>
        </td>
    </tr>
</table>